# OMMX Adapterで初期解を利用する方法

OMMX Adapterの中には、最適化計算実行時に初期解を渡す機能をサポートしているものがあります。ここではOMMXPySCIPOptAdapterを例に、この機能を紹介します。初期解を渡すことで、ソルバーが初期実行可能解を自ら構築する必要がなくなり、最適化計算のパフォーマンスが向上することがあります。

## 初期解を渡す方法

渡すことのできる初期解（initial_state）は`ToState`型であり、これは`ommx.v1.State`または`Mapping[int, float]`の両方の型を受け取ることができます。
以下のインスタンスを用いて、初期解を渡す方法を説明します。

In [ ]:
from ommx.v1 import Instance, DecisionVariable
from ommx.v1.solution_pb2 import State

x = DecisionVariable.integer(1, lower=0, upper=5)
y = DecisionVariable.integer(2, lower=0, upper=5)

ommx_instance = Instance.from_components(
    decision_variables=[x, y],
    objective=x - y,
    constraints=[x + y <= 5],
    sense=Instance.MAXIMIZE,
)

`ommx.v1.State`による初期解の例

In [ ]:
initial_state = State(
    entries={
        1: 3.0,
        2: 2.0,
    }
)

`Mapping[int, float]`による初期解の例

In [ ]:
initial_state = {
    1: 3.0,
    2: 2.0,
}

以下の通り、solve関数に`initial_state`を引数として渡すことで、初期解を渡して最適化計算を実行することができます。

In [ ]:
from ommx_pyscipopt_adapter import OMMXPySCIPOptAdapter

solution = OMMXPySCIPOptAdapter.solve(
    ommx_instance=ommx_instance,
    initial_state=initial_state,
)

ソルバーをチューニングして利用したい場合、直接OMMXPySCIPOptAdapterクラスを使うことでソルバーのパラメーター等を設定するケースもあります。この場合においても、以下の通り`initial_state`を引数として渡すことができます。

In [ ]:
from ommx_pyscipopt_adapter import OMMXPySCIPOptAdapter

adapter = OMMXPySCIPOptAdapter(
    ommx_instance=ommx_instance,
    initial_state=initial_state,
)

## 初期解の有無による比較の例

MIPLIBの`roll3000`というインスタンスを例に、初期解を渡す場合と渡さない場合で、どのような違いが生じるかを確認します。
初期解としては、事前に作成しておいた実行可能解（最適解ではない）を与えることとします。

In [ ]:
from ommx_pyscipopt_adapter import OMMXPySCIPOptAdapter
from ommx import dataset

# インスタンスの読み込み
ommx_instance = dataset.miplib2017("roll3000")

### 初期解を渡さない場合

In [ ]:
import time

start = time.perf_counter()
solution = OMMXPySCIPOptAdapter.solve(
    ommx_instance=ommx_instance,
)
duration = time.perf_counter() - start
print(f"実行時間: {duration}")

### 初期解を渡す場合

初期解（initial_state）として、このチュートリアルでは事前に得られた以下を使用することとします。

In [ ]:
initial_state = {257: -1.84297022087776e-14, 703: 0.0, 531: -4.6407322429331543e-14, 1052: -9.621932880084689e-15, 360: 0.0, 175: 0.0, 507: 11.000000000000002, 301: 0.0, 937: 3.0000000000000044, 859: 0.0, 564: -3.1086244689504383e-15, 557: -4.6407322429331543e-14, 205: 0.0, 617: 1.3322676295501878e-14, 162: 0.0, 811: 0.0, 759: 3.1086244689503373e-15, 682: 0.0, 987: 0.0, 1013: 0.0, 536: 0.9999999999998973, 189: 0.0, 540: -4.440892098500626e-15, 1135: 0.0, 1163: 0.0, 526: 0.0, 7: -5.362970457884017e-15, 83: 2.0, 606: 0.0, 677: 1.000000000000089, 935: 0.0, 224: 0.0, 824: -5.551115123115685e-17, 161: 0.0, 671: 0.9999999999999867, 1075: 0.0, 1147: 4.440892098500626e-15, 107: -2.6645352591003757e-15, 807: 0.0, 836: 0.0, 1110: 0.0, 1143: 0.0, 84: 0.0, 368: 4.218847493575595e-14, 639: 0.0, 663: 0.0, 171: 0.0, 423: 3.0000000000001226, 730: 0.0, 21: 0.0, 931: -8.881784197001252e-15, 611: 2.842170943040401e-14, 833: 0.0, 435: 4.000000000000141, 410: 0.0, 505: 3.000000000000361, 198: 0.0, 262: 0.0, 76: 0.0, 620: -8.881784197001252e-15, 616: 0.0, 95: -3.887299665209862e-15, 291: 0.0, 748: 2.842170943040401e-14, 822: 1.1435297153639112e-14, 450: 0.0, 61: 0.0, 1003: 3.999999999999979, 845: 2.000000000000089, 124: 0.9999999999999991, 1031: 0.0, 716: 0.0, 948: 5.999999999999996, 821: 0.0, 493: 0.0, 212: 0.0, 34: 0.0, 136: 2.999999999999928, 20: 1.0000000000000009, 701: -8.881784197001252e-15, 839: 0.0, 246: 0.0, 282: 0.0, 919: 0.0, 418: 0.0, 967: 0.0, 1099: 0.0, 458: 0.0, 342: 0.0, 452: 0.0, 637: 0.0, 233: 3.000000000000105, 138: 0.0, 857: 1.000000000000047, 487: -2.6645352591003757e-15, 275: 0.0, 964: 3.0000000000000124, 447: 1.0, 622: 0.0, 877: 0.0, 242: 0.0, 596: 0.0, 854: -1.865174681370263e-14, 153: 1.0000000000000286, 478: 0.0, 679: 2.9999999999999494, 1125: 0.0, 612: 0.0, 975: 0.0, 943: 0.0, 1009: 0.0, 829: 0.0, 400: 0.0, 321: 0.0, 1054: 1.865174681370263e-14, 1159: 1.9999999999999867, 471: -3.1086244689504383e-15, 797: -2.7533531010703882e-14, 1074: -4.3520742565306136e-14, 714: -3.019806626980426e-14, 1162: 0.0, 299: 0.0, 645: 0.0, 71: 0.0, 858: 5.000000000000172, 306: 1.0, 861: 1.84297022087776e-14, 172: 0.0, 1028: 8.881784197001252e-16, 808: 0.0, 1114: 3.9999999999999725, 134: 4.440892098500626e-14, 646: 0.0, 1080: 10.0, 393: -2.4868995751603507e-14, 55: 0.0, 110: 0.0, 949: 3.0531133177191805e-15, 373: 0.0, 456: 0.0, 856: -4.440892098500625e-16, 708: 0.0, 430: 0.0, 560: 0.0, 1017: 2.930988785010413e-14, 243: 1.887379141862766e-14, 971: 2.0000000000000666, 402: 0.9999999999999574, 37: 0.0, 324: 1.000000000000021, 1030: 0.0, 984: 0.0, 749: 8.881784197001252e-15, 250: 0.0, 472: 0.0, 177: 1.0000000000000315, 82: 7.105427357601002e-15, 333: 0.0, 1096: -1.0725940915768033e-14, 372: 4.884981308350689e-14, 140: 0.0, 652: 0.0, 60: 0.0, 316: 0.0, 785: 0.0, 432: 0.0, 401: 0.0, 513: 0.0, 309: 0.0, 633: 1.9999999999999853, 951: 0.0, 481: 3.7192471324942744e-14, 240: 1.000000000000007, 599: 0.0, 685: 0.0, 610: 0.0, 690: 0.9999999999999996, 500: 0.0, 252: 0.0, 603: 0.0, 853: 1.0000000000000089, 519: 0.0, 827: 2.0, 823: 7.000000000000012, 602: 0.0, 578: 0.0, 1064: -4.3520742565306136e-14, 215: 8.881784197001252e-16, 85: 0.0, 583: 0.0, 650: -8.926193117986259e-14, 517: 0.0, 412: 0.0, 609: 0.0, 1133: 1.9999999999999196, 1079: 0.0, 576: 0.0, 803: 0.0, 832: 0.0, 1066: 4.1744385725905886e-14, 694: 1.0, 408: 0.0, 315: 0.0, 783: 0.0, 1127: 0.0, 998: 0.0, 462: 1.0, 1034: 0.0, 678: 1.687538997430238e-14, 454: 0.0, 511: 0.0, 925: 0.0, 707: -3.647082635893639e-14, 411: 0.0, 618: 0.0, 46: 1.000000000000011, 891: 0.0, 740: 0.0, 121: 0.0, 2: 0.0, 459: 0.9999999999999853, 774: 0.0, 339: 1.0000000000000115, 334: 0.0, 669: -7.993605777301127e-15, 255: 0.0, 390: 0.0, 587: 1.000000000000007, 835: 0.0, 133: -1.7985612998927536e-14, 396: 0.0, 341: 0.0, 382: 2.999999999999912, 428: 0.0, 761: 2.220446049250313e-15, 99: 0.0, 156: 0.0, 589: 198.99999999999935, 621: 1.0000000000000009, 510: -9.386431026376354e-16, 687: 0.0, 1156: 0.0, 915: 2.842170943040401e-14, 1051: 0.0, 328: 0.0, 882: 0.0, 258: -1.84297022087776e-14, 1158: 0.0, 995: 1.9999999999999565, 636: -9.175151694187626e-17, 966: -3.1086244689504383e-15, 199: 0.0, 781: 0.0, 754: 0.0, 249: -2.6645352591003757e-15, 969: 0.0, 985: 0.0, 1055: 0.0, 961: 0.0, 141: 2217.9999999999973, 641: 0.0, 607: 0.0, 973: -3.887299665209862e-15, 630: 2.930988785010413e-14, 444: 1.0, 689: 0.0, 89: 0.0, 41: 0.0, 126: 0.0, 69: 0.0, 343: -5.362970457884017e-15, 1021: 0.0, 466: 1.0, 217: -8.881784197001252e-16, 902: 0.0, 604: 67.00000000000283, 539: 1.0047518372857667e-13, 876: 0.0, 534: 0.0, 414: 0.0, 720: 0.0, 911: 0.0, 1070: 0.0, 23: 0.0, 798: 0.0, 1142: -3.1086244689504383e-15, 791: 0.0, 119: 0.0, 615: 1.0, 795: 1.0, 417: 0.0, 59: -9.2148511043888e-15, 755: 1.0000000000000009, 286: 1.9999999999999485, 760: 0.0, 194: 2.0000000000001297, 139: 0.0, 533: 1.0, 608: 0.0, 463: 1.0000000000000364, 965: 5.000000000000172, 665: 0.0, 886: 0.0, 1145: 0.0, 326: 0.0, 453: 0.0, 1104: -1.5765166949677223e-14, 844: 0.0, 903: 0.0, 144: 0.0, 1023: 0.0, 775: 0.0, 884: 0.0, 739: 0.0, 776: 0.0, 308: -8.881784197001252e-15, 851: 4.218847493575595e-15, 294: 0.0, 247: 0.0, 1062: 1.0000000000000364, 125: 1.0000000000000102, 446: 0.0, 366: 0.0, 64: 0.0, 268: 0.0, 757: 0.0, 168: 0.0, 303: 0.0, 688: -2.6645352591003757e-15, 490: 0.0, 590: 0.0, 195: -3.1086244689504383e-15, 506: 1.3322676295501878e-14, 152: 0.0, 380: 1.0, 421: 1.0, 216: 0.0, 327: 0.0, 1015: 0.0, 312: 0.0, 1032: 0.0, 743: 1.0, 1040: 0.0, 176: 0.0, 376: 0.0, 314: 0.0, 165: 0.0, 159: 0.0, 1071: 1.0, 67: 0.0, 1121: -8.722144284963535e-15, 386: 0.9999999999999867, 696: 1.0000000000000004, 538: 0.0, 214: 0.0, 710: 0.0, 515: 0.0, 1082: -1.1102230246251565e-16, 979: 0.0, 94: -5.2004562015845005e-15, 527: 0.0, 102: 0.0, 982: 0.0, 100: 3.0000000000000124, 123: 0.0, 483: 0.0, 167: 1.0, 537: 0.0, 686: 0.0, 280: 3.9999999999999956, 293: 0.0, 672: 151.9999999999999, 191: 0.0, 896: 0.0, 997: 0.0, 92: 0.0, 873: 0.0, 237: 1.0000000000000102, 26: 0.0, 732: -6.217248937900877e-15, 469: 1.0, 959: 0.0, 485: 3.000000000000033, 974: 0.0, 799: 0.0, 750: 0.0, 43: 1.0, 711: 161.9999999999928, 548: 0.0, 362: 0.0, 787: 0.0, 244: 0.0, 24: 0.0, 96: 1.0000000000000284, 588: 0.0, 908: 0.0, 626: 0.0, 762: 0.9999999999999916, 234: 0.0, 1004: 0.0, 489: 0.0, 379: 2.9999999999998863, 651: 0.0, 623: 1.4210854715202004e-14, 1025: 1.0, 488: 0.0, 940: -2.6513460148478883e-14, 461: 0.0, 862: 0.0, 529: 3.197442310920451e-14, 8: 0.0, 950: 1.0000000000000158, 544: 0.0, 499: 0.0, 27: 29.99999999999986, 613: 0.9999999999998973, 521: 0.0, 993: 0.0, 784: -1.4223963249031613e-16, 10: 0.0, 477: -1.3322676295501877e-15, 747: 9.947598300641403e-14, 929: 0.0, 1018: 0.0, 986: 0.0, 562: 0.0, 185: 0.0, 594: 0.0, 726: 0.0, 129: -2.752545508256288e-16, 1024: 1.0000000000001048, 356: 0.9999999999999707, 201: 0.0, 455: 0.0, 436: 0.9999999999999707, 14: -8.548717289613705e-15, 354: 12889.999999999976, 498: 0.0, 860: 0.0, 643: 0.0, 12: -2.6645352591003757e-15, 468: 32.000000000000014, 605: 1.0000000000000278, 190: 0.0, 359: 0.0, 614: 0.0, 289: 0.0, 1022: 0.0, 434: 0.0, 479: -1.5765166949677223e-14, 572: 1.3322676295501878e-14, 1014: 0.0, 114: 0.0, 737: 0.0, 348: 2.1316282072803006e-14, 265: 0.0, 741: -5.400124791776761e-13, 169: 0.0, 825: 0.0, 1049: 4.440892098500626e-15, 561: 0.0, 1044: 0.0, 358: 0.9999999999999831, 1085: 2.999999999999983, 920: -8.881784197002262e-16, 281: 0.0, 1043: 0.0, 654: 0.0, 901: -1.6241245636507983e-14, 648: 2.9999999999999414, 397: -4.440892098500626e-15, 907: 197.00000000000014, 1124: 0.0, 1063: 1.0, 697: 0.0, 1086: 4.000000000000141, 728: -4.2549297418759124e-14, 403: 0.0, 6: 0.0, 913: 0.0, 228: 1.0047518372857667e-13, 442: 8.881784197001252e-16, 994: 0.0, 208: 0.0, 815: 0.0, 698: 0.0, 518: 0.0, 197: -1.021405182655144e-14, 934: 2.999999999999903, 591: -1.0725940915768033e-14, 439: 0.0, 443: 0.0, 1047: 0.0, 894: -3.7192471324942744e-15, 184: 0.0, 1128: 0.0, 70: 0.0, 492: 0.0, 782: 1.2156942119645464e-14, 516: 0.0, 1151: 0.0, 1097: 95.0, 101: 1.7763568394002505e-14, 976: 0.0, 352: 0.0, 151: 4.3115457266996746e-17, 270: 0.0, 1073: -3.4181831865424275e-16, 751: 0.0, 864: 0.0, 351: 0.0, 939: 0.0, 433: 0.0, 756: -4.440892098500627e-16, 30: 0.0, 166: 1.2156942119645464e-14, 955: 0.0, 241: 0.9999999999999999, 1132: 0.0, 658: 0.0, 1036: 0.0, 887: 279.9999999999998, 866: 4.063416270128073e-14, 311: 0.0, 655: 0.0, 753: 2.0, 35: 0.0, 962: 0.0, 385: -1.1435297153639112e-14, 335: 0.9999999999999987, 1057: 0.0, 674: 1.0000000000000884, 388: 1.0, 921: 1.9999999999999498, 264: 0.0, 972: 8.881784197001252e-15, 75: -8.881784197002262e-16, 15: 0.0, 344: 0.0, 528: 0.0, 780: 0.0, 1134: 0.0, 530: 0.0, 44: 0.0, 135: 2.968534766042603e-14, 771: 0.0, 649: 0.0, 1093: 0.0, 220: 0.0, 898: -3.647082635893639e-14, 305: 0.0, 1140: 0.0, 395: 0.0, 870: -3.019806626980426e-14, 905: 1.0000000000000435, 1008: 0.9999999999999813, 837: -5.2004562015845005e-15, 1011: 1.865174681370263e-14, 63: 0.0, 1006: 0.0, 673: 1.4210854715202004e-14, 960: 0.0, 627: 0.0, 378: 0.0, 399: 0.0, 132: 0.0, 475: 0.0, 319: 0.0, 735: 2.6513460148478883e-14, 4: 0.0, 419: 0.0, 1077: 3.9999999999999485, 582: 1.000000000000011, 550: 0.0, 881: 9.769962616701378e-15, 371: 1.0000000000000469, 676: 0.0, 553: 1.0, 229: 0.0, 155: 0.0, 1060: 0.0, 988: 0.0, 644: 7.993605777301127e-15, 357: 0.0, 638: 0.0, 56: -7.105427357601002e-15, 802: 0.0, 834: 0.0, 1045: 8.881784197001252e-16, 3: 0.0, 496: 0.0, 290: 0.0, 922: 0.0, 186: 0.0, 868: 0.0, 457: 0.0, 480: 0.0, 248: 0.9999999999999981, 1105: 0.0, 661: 2.220446049250313e-14, 106: 0.0, 1103: -8.881784197001252e-15, 1026: 0.0, 266: 1.0000000000000007, 424: 0.0, 956: 0.0, 778: 0.0, 668: 0.0, 325: 0.0, 692: 1.0047518372857667e-13, 952: 8.000000000000055, 323: 1.865174681370263e-14, 695: 0.9999999999999929, 942: 0.0, 374: 2.220446049250313e-15, 188: 0.0, 1107: 0.0, 712: 0.0, 767: 0.0, 150: -2.0261570199409107e-14, 938: 0.9999999999999991, 187: -1.3377022877126888e-14, 543: 0.0, 1102: 1.0000000000000018, 300: 0.0, 916: 1.0000000000000302, 330: -2.6645352591003757e-14, 36: 0.0, 1078: 0.0, 532: 1.0, 888: 30.000000000000682, 1067: 0.0, 347: 0.0, 429: 0.9999999999999999, 448: 0.0, 437: 0.0, 1095: 0.0, 284: 1.0, 431: 0.0, 9: 1.3322676295501878e-14, 725: 1.000000000000089, 1098: 0.0, 451: 1.9999999999999565, 81: 0.0, 667: 1.000000000000011, 570: -8.881784197001252e-16, 779: 9.202150330924782e-17, 54: 0.0, 22: 0.0, 404: 0.0, 235: 0.0, 542: 0.0, 118: 0.0, 805: 0.0, 398: 0.0, 878: 0.0, 226: -1.3377022877126888e-14, 78: 3.999999999999904, 909: -7.993605777301127e-15, 1012: 0.0, 814: 0.0, 524: 3.0000000000000115, 238: 0.0, 566: -2.6645352591003757e-15, 554: 0.0, 675: 0.0, 923: 0.0, 874: 0.0, 559: 0.0, 1154: 0.0, 1089: 1.7763568394002505e-15, 551: 0.0, 391: 0.0, 883: 0.0, 203: 0.0, 285: 1.999999999999993, 269: 0.0, 792: 1.0, 659: 0.0, 160: 2.000000000000005, 279: 0.0, 148: 2.0000000000000187, 702: 7.105427357601002e-15, 80: 0.0, 555: 0.0, 11: 0.0, 958: 0.0, 473: 0.0, 182: 0.0, 1138: 0.0, 427: 0.0, 231: 3.0000000000000213, 926: 0.0, 895: 0.0, 968: 0.0, 954: 0.0, 389: 0.0, 223: -5.684341886080802e-14, 329: 1.0, 800: 3.730349362740526e-14, 164: 0.0, 1058: 0.0, 1029: 0.0, 773: 0.0, 790: 0.0, 58: 0.0, 597: 0.0, 547: 0.0, 812: 0.0, 1002: -8.750737653510993e-14, 340: 4.999999999999949, 1094: 0.9999999999999973, 625: 2.9999999999999893, 804: 0.9999999999999996, 1088: 1.9999999999999885, 345: 1.000000000000089, 717: 1.000000000000031, 558: 0.0, 304: 0.9999999999999901, 867: 8.000000000000055, 253: 33.00000000000008, 765: 0.0, 1117: 0.0, 927: 2.9999999999999627, 202: 0.0, 1007: 0.0, 1108: 0.0, 355: 0.0, 1150: 0.0, 917: 4.999999999999981, 387: 8.43769498715119e-15, 632: 0.0, 192: 0.0, 1139: 0.0, 1160: 1.9999999999999898, 1141: 0.0, 843: 0.0, 48: 2.999999999999967, 830: 137.99999999999926, 1122: 0.0, 245: -1.0502709812953981e-13, 120: 0.0, 349: 0.0, 17: 9.2148511043888e-15, 642: 0.0, 200: 1.0, 912: 2.0000000000000187, 699: 238.00000000000003, 1129: 0.0, 724: 0.0, 992: 3.064215547965432e-14, 112: 0.0, 416: 187.00000000000009, 684: 0.0, 706: 0.0, 174: 4.000000000000132, 546: 0.0, 97: 0.0, 465: 2.3426113579956395e-16, 298: 0.0, 445: 0.9999999999999902, 733: 1.000000000000089, 1090: 0.0, 86: 0.0, 422: 0.0, 236: 0.0, 318: 8.43769498715119e-15, 232: 0.0, 31: 0.0, 273: 0.0, 810: 0.0, 764: 0.0, 1119: 0.9999999999999971, 1048: 0.0, 872: 15.000000000000012, 818: 0.0, 1101: 0.0, 653: 1.0, 384: 0.0, 297: 0.0, 777: -1.7985612998927536e-14, 145: -2.0261570199409107e-14, 127: -8.881784197001252e-16, 79: 0.0, 953: 0.0, 73: 0.0, 90: -8.881784197001252e-15, 363: 0.0, 502: 0.0, 227: -8.548717289613705e-15, 525: 2601.999999999994, 251: 0.0, 98: 2.842170943040401e-14, 211: 0.0, 13: 0.0, 470: 1.9999999999999947, 108: 0.0, 1136: 0.0, 310: 0.0, 426: 6.999999999999999, 892: 1.0000000000000941, 440: 0.0, 841: -3.7192471324942744e-14, 850: 0.0, 552: 0.0, 584: 1.0, 367: 0.0, 629: 0.0, 494: 0.0, 889: 0.0, 464: 9.325873406851315e-14, 259: 0.0, 375: 0.0, 353: 0.0, 598: 1.0000000000000213, 631: 3.000000000000022, 577: 0.0, 704: 0.0, 93: 0.0, 746: 0.0, 565: -2.6645352591003757e-15, 963: 0.0, 1050: 1.0, 1083: 0.0, 292: 1.000000000000023, 332: 0.0, 1100: 0.0, 693: 0.0, 990: 0.0, 512: 0.0, 601: 2.0000000000000355, 713: -8.903988657493755e-14, 369: 0.0, 0: 8.881784197001252e-16, 1081: 1.3322676295501878e-14, 541: 1.0, 196: 0.0, 681: 0.0, 213: 0.0, 467: 0.0, 474: -8.926193117986259e-14, 50: 0.9999999999999574, 1152: -1.674216321134736e-13, 1137: 1.000000000000105, 885: 2.999999999999928, 786: 1.0000000000000007, 817: 12889.999999999976, 130: 0.0, 137: 1.0, 53: 1.0000000000000315, 495: 0.0, 441: 0.0, 571: 1.865174681370263e-14, 1115: 8.881784197001252e-16, 809: 0.0, 819: -9.769962616701378e-15, 1165: 0.0, 364: 0.0, 261: 74.00000000000007, 535: 0.0, 848: 0.0, 731: 0.0, 945: 0.0, 624: 5.000000000000172, 1106: 0.0, 772: 1.000000000000007, 460: 0.0, 727: 0.0, 1046: 0.0, 394: 0.0, 267: -2.7411935155625904e-15, 842: 0.0, 49: 4.999999999999921, 930: 1.999999999999993, 670: 0.0, 928: 0.0, 924: 0.0, 691: 0.0, 146: 0.0, 25: 0.0, 491: 0.0, 142: 9.947598300641403e-14, 849: 0.0, 932: 0.9999999999999867, 33: 1.0, 1010: 0.9999999999999005, 409: 7.105427357601002e-15, 350: 0.0, 207: 2.0000000000000187, 1084: 0.0, 918: -3.7192471324942744e-15, 1112: 0.0, 1016: 0.0, 1053: 0.0, 508: 1.0047518372857667e-13, 482: 0.0, 944: 0.0, 789: 0.0, 1076: 2.9999999999999813, 52: 1.4210854715202004e-14, 680: -7.438494264988549e-15, 320: -8.548717289613705e-15, 449: -2.4868995751603507e-14, 1037: 0.0, 317: 1.000000000000028, 855: 0.9999999999999973, 277: 0.0, 758: 4.440892098500626e-15, 91: 0.0, 222: 0.0, 29: 0.0, 567: 0.0, 438: -6.078471059822732e-15, 549: 0.9999999999999707, 763: 0.0, 991: 4.440892098500626e-15, 628: 0.0, 1068: 0.0, 936: 0.0, 178: 1.0000000000000002, 256: 0.0, 831: 0.0, 183: -8.881784197001252e-16, 1164: 0.0, 946: 0.0, 580: 0.0, 838: 0.0, 19: 0.0, 18: 3.00000000000004, 88: 0.9999999999999999, 420: -3.552713678800501e-15, 377: 0.0, 425: 4.00000000000001, 662: 1.6105119292618043e-14, 806: 0.0, 370: 0.0, 87: -2.930988785010413e-14, 287: 0.0, 579: 0.0, 154: 0.0, 794: 0.0, 501: 7.000000000000055, 852: 1.0000000000000009, 744: 0.0, 1120: 0.0, 406: 0.9999999999999947, 1157: 0.0, 556: 0.0, 103: 1.000000000000018, 1161: 0.0, 666: 0.0, 705: 0.0, 592: 0.0, 47: 0.0, 128: 144.00000000000003, 977: -8.881784197001252e-15, 57: -1.0658141036401503e-14, 503: 0.0, 1144: 0.0, 900: 0.0, 647: 0.0, 68: 0.0, 595: 0.0, 575: 0.0, 415: 0.0, 288: 0.0, 39: 2.9999999999999956, 381: 0.0, 906: 0.0, 846: 1.0, 218: 1.0, 42: -7.993605777301127e-15, 514: 4.440892098500626e-14, 1091: 337.00000000000006, 664: 0.0, 523: 1.0000000000000226, 193: 4.440892098500626e-15, 74: 0.9999999999998995, 263: 0.0, 1027: 0.0, 593: 0.0, 170: 0.0, 1000: -1.2434497875801753e-14, 338: 1.0000000000000115, 1126: 2.6645352591003757e-15, 113: 0.0, 683: 0.0, 715: 0.0, 486: 0.0, 407: 0.0, 66: 0.0, 1148: 0.0, 914: 0.0, 718: -1.3322676295501877e-15, 115: 0.0, 1155: 0.0, 230: 0.0, 826: 0.0, 278: 1.0000000000000286, 999: 0.0, 947: 0.0, 1118: 0.0, 828: -2.930988785010413e-14, 634: 0.0, 1123: 0.0, 721: 0.0, 117: 0.0, 1116: 0.0, 719: -7.993605777301127e-15, 392: 0.0, 405: 2.0000000000000187, 880: 1.000000000000089, 520: 2.784308972829587e-15, 210: 0.0, 1061: 1.0, 793: 0.0, 504: 0.0, 1072: 0.0, 989: 0.0, 813: 0.0, 1042: 1.9999999999999885, 752: 8.881784197001252e-16, 700: 0.0, 1041: 2.0000000000000204, 413: 1.3322676295501878e-14, 574: 3.0000000000000018, 736: 0.0, 1113: 0.0, 904: 0.0, 173: 0.0, 1056: 5.000000000000033, 295: 1.0000000000000278, 619: 2.0, 5: 0.9999999999999951, 497: 0.0, 635: 1.0, 1065: 0.0, 788: 0.0, 742: 1.0, 1039: 0.9999999999999427, 522: 2.220446049250313e-16, 1038: 0.0, 180: 1.0000000000000469, 729: 0.9999999999999628, 869: 0.0, 820: 1.9999999999999982, 219: 0.0, 981: 8.881784197001252e-16, 1020: 1.000000000000089, 147: 0.0, 933: 0.0, 723: 10.000000000000068, 879: 212.00000000000003, 149: 0.0, 509: 1.0, 72: 0.0, 111: 0.0, 897: 3.7192471324942744e-14, 163: 0.0, 978: 1.000000000000047, 1109: 0.0, 545: 0.9999999999999853, 143: 0.9999999999999947, 337: 0.9999999999999005, 302: 1.999999999999993, 1149: 0.0, 840: 0.0, 283: 2.0000000000000204, 271: 0.0, 1019: 0.0, 769: 1.7763568394002505e-15, 16: 0.9999999999999707, 893: -4.6851411639181606e-14, 1092: 0.0, 331: 0.0, 865: 1.3322676295501878e-14, 1001: 2.0, 660: 0.0, 1111: 1.0, 204: 1.0000000000000187, 383: 0.0, 105: 10.000000000000002, 77: 0.0, 734: 1.0, 45: 0.0, 209: 1.0000000000000382, 657: 0.0, 131: 0.0, 1131: -8.881784197001252e-15, 709: 8.881784197001252e-15, 1: 0.0, 957: -1.84297022087776e-14, 656: 0.0, 476: 0.9999999999999694, 104: 0.0, 296: 0.0, 980: 0.0, 62: 0.0, 1130: 0.0, 847: 5.000000000000135, 1035: 0.0, 1146: 0.0, 361: 3.0000000000000124, 768: 0.0, 157: 0.0, 875: 0.0, 890: 0.0, 109: 3.0000000000000044, 585: 1.0, 28: 0.0, 796: 0.0, 365: 0.0, 983: 7.993605777301127e-15, 586: 0.0, 158: 0.0, 600: 2.0000000000000187, 910: 0.0, 179: 0.0, 65: 0.0, 581: 5.000000000000054, 941: 0.0, 722: -3.785860513971784e-14, 1069: 0.0, 1059: 0.0, 346: 0.0, 181: 1.0000000000000364, 307: -1.865174681370263e-14, 568: 0.0, 38: 1.0, 970: 0.0, 40: 4.440892098500626e-15, 738: 0.0, 276: 0.0, 274: 0.0, 871: 0.0, 272: 1.0, 260: 0.0, 801: 0.0, 239: 1.9999999999998908, 322: 0.0, 206: 0.0, 116: 0.0, 766: 0.0, 816: 0.0, 225: 0.9999999999998995, 770: -6.022959908591474e-15, 563: 0.0, 336: 0.0, 573: -9.386431026376354e-16, 254: 0.0, 122: 0.0, 899: -4.440892098500627e-16, 1087: 0.0, 745: 0.0, 640: 0.0, 313: -4.263256414560601e-14, 1153: 0.0, 996: 0.9999999999999498, 51: 0.0, 1033: 0.0, 863: 0.0, 32: 1.000000000000003, 484: 1.000000000000028, 1005: -1.021405182655144e-14, 569: 9.473903143468002e-15, 221: 0.0}

`initial_state`を渡してsolveを実行する

In [ ]:
start = time.perf_counter()
solution = OMMXPySCIPOptAdapter.solve(
    ommx_instance=ommx_instance,
    initial_state=initial_state,
)
duration = time.perf_counter() - start
print(f"実行時間: {duration}")

この例では、初期解を渡すことで、最適化計算に要する時間が短縮されました。
なお、初期解を渡すことで常にパフォーマンスが向上するわけではなく、変動がなかったり、悪化するケースもあります。このため、向上するか否かについて試行錯誤は必要ですが、有効なケースにおいては大きなパフォーマンスの向上が期待できます。